In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import re
from gensim.models import Word2Vec
import datetime

C:\Users\Lassana Diabira\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
df=pd.read_csv("data.csv")

C:\Users\Lassana Diabira\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2785: DtypeWarning: Columns (2,3,6,7,8,9,12,13,14,15,17,19,21,23) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
df['job_created_date'] =  pd.to_datetime(df['job_created_date'])
df['job_opening_date'] =  pd.to_datetime(df['job_opening_date'])
df['job_closing_date'] =  pd.to_datetime(df['job_closing_date'])

In [4]:
df.head()

Unnamed: 0  user_id    job_created_date job_application_status  job_id  \
0           0  75898.0 2017-09-01 01:00:02              Initiated   214.0   
1          11  75898.0 2017-09-01 01:00:02              Initiated   214.0   
2          10  75898.0 2017-09-01 01:00:02              Initiated   214.0   
3           9  75898.0 2017-09-01 01:00:02              Initiated   214.0   
4       23304  75898.0 2017-09-01 01:00:02              Initiated   214.0   

   employer_id job_opening_date job_closing_date  \
0         25.0       2017-03-27       2017-08-31   
1         25.0       2017-03-27       2017-08-31   
2         25.0       2017-03-27       2017-08-31   
3         25.0       2017-03-27       2017-08-31   
4         25.0       2017-03-27       2017-08-31   

                               job_short_description  \
0  Think of our Summer Vacation Scheme in 2018 as...   
1  Think of our Summer Vacation Scheme in 2018 as...   
2  Think of our Summer Vacation Scheme in 2018 as...   
3  Think of our Summer Vacation Scheme in 2018 as...   
4  Think of our Summer Vacation Scheme in 2018 as...   

                                     job_description  \
0  <p>Apply now to fast track your application to...   
1  <p>Apply now to fast track your application to...   
2  <p>Apply now to fast track your application to...   
3  <p>Apply now to fast track your application to...   
4  <p>Apply now to fast track your application to...   

             ...             course_includes_industrial_placement  \
0            ...                                            False   
1            ...                                            False   
2            ...                                            False   
3            ...                                            False   
4            ...                                            False   

   graduation_year right_to_work_uk degree_subject_id university_id  \
0           2019.0             True            1371.0         381.0   
1           2019.0             True            1371.0         381.0   
2           2019.0             True            1371.0         381.0   
3           2019.0             True            1371.0         381.0   
4           2019.0             True            1371.0         381.0   

            university_name  university_type   degree_subject_name  \
0  University of Manchester              2.0  Spanish and Business   
1  University of Manchester              2.0  Spanish and Business   
2  University of Manchester              2.0  Spanish and Business   
3  University of Manchester              2.0  Spanish and Business   
4  University of Manchester              2.0  Spanish and Business   

   degree_subjectgroup_id degree_subjectgroup_title  
0                    26.0          Modern Languages  
1                    26.0          Modern Languages  
2                    26.0          Modern Languages  
3                    26.0          Modern Languages  
4                    19.0   Business and Management  

[5 rows x 31 columns]

In [5]:
df=df[df.user_id.notnull()]

In [6]:
df.shape

(976689, 31)

In [7]:
def get_jobs_per_user(df):
    users_id=df.user_id.values
    users_id=list(set(users_id))
    n=len(users_id)
    print("users collected")
    jobs_per_user={}
    for i,user in enumerate(users_id):
        if i%100000:
            print("progress :", i/n)
        x=df[df["user_id"]==user]
        x=x[x.job_id.notnull()]
        if x.shape[0]>0:
            job_applications=x["job_id"].values
            job_applications=list(set(job_applications))
            jobs_per_user[str(int(user))]=job_applications
    print("Jobs per user collected")
    return jobs_per_user

In [8]:
jobs_per_user=get_jobs_per_user(df)

users collected
Jobs per user collected


In [9]:
def get_jobs_to_recommend(df,jobs_per_user):
    users_id=df.user_id.values
    users_id=list(set(users_id))
    n=len(users_id)
    recommendations_per_user={}
    print("users collected")
    now = datetime.datetime.now()
    d=df[df['job_closing_date']<=now]
    d=d[d.job_id.notnull()]
    jobs_to_apply_to=d["job_id"].values
    print("recommendations started")
    for i,user in enumerate(users_id):
        if i%100000:
            print("progress :", i/n)
        try:
            job_applications=jobs_per_user[str(int(user))]
            recommendations=list(set(jobs_to_apply_to) - set(job_applications))
            recommendations_per_user[str(int(user))]=recommendations
        except:
            pass
    return recommendations_per_user

In [10]:
recommendations_per_user=get_jobs_to_recommend(df, jobs_per_user)

users collected
recommendations started
progress : 6.029508414178992e-06
progress : 1.2059016828357985e-05
progress : 1.8088525242536974e-05
progress : 2.411803365671597e-05
progress : 3.014754207089496e-05
progress : 3.617705048507395e-05
progress : 4.2206558899252944e-05
progress : 4.823606731343194e-05
progress : 5.426557572761093e-05
progress : 6.029508414178992e-05
progress : 6.632459255596892e-05
progress : 7.23541009701479e-05
progress : 7.838360938432689e-05
progress : 8.441311779850589e-05
progress : 9.044262621268488e-05
progress : 9.647213462686388e-05
progress : 0.00010250164304104286
progress : 0.00010853115145522185
progress : 0.00011456065986940085
progress : 0.00012059016828357984
progress : 0.00012661967669775882
progress : 0.00013264918511193783
progress : 0.00013867869352611681
progress : 0.0001447082019402958
progress : 0.0001507377103544748
progress : 0.00015676721876865378
progress : 0.0001627967271828328
progress : 0.00016882623559701177
progress : 0.000174855744

progress : 0.0042930099908954425
progress : 0.004299039499309622
progress : 0.004305069007723801
progress : 0.004311098516137979
progress : 0.004317128024552158
progress : 0.004323157532966337
progress : 0.004329187041380516
progress : 0.004335216549794695
progress : 0.004341246058208874
progress : 0.0043472755666230534
progress : 0.0043533050750372325
progress : 0.004359334583451412
progress : 0.00436536409186559
progress : 0.004371393600279769
progress : 0.004377423108693948
progress : 0.004383452617108127
progress : 0.004389482125522306
progress : 0.004395511633936485
progress : 0.004401541142350664
progress : 0.0044075706507648435
progress : 0.0044136001591790226
progress : 0.004419629667593201
progress : 0.00442565917600738
progress : 0.004431688684421559
progress : 0.004437718192835738
progress : 0.004443747701249917
progress : 0.004449777209664096
progress : 0.004455806718078275
progress : 0.004461836226492454
progress : 0.0044678657349066335
progress : 0.004473895243320812
prog

progress : 0.008815141301529687
progress : 0.008821170809943865
progress : 0.008827200318358045
progress : 0.008833229826772223
progress : 0.008839259335186402
progress : 0.008845288843600582
progress : 0.00885131835201476
progress : 0.00885734786042894
progress : 0.008863377368843118
progress : 0.008869406877257298
progress : 0.008875436385671476
progress : 0.008881465894085656
progress : 0.008887495402499834
progress : 0.008893524910914012
progress : 0.008899554419328192
progress : 0.00890558392774237
progress : 0.00891161343615655
progress : 0.008917642944570729
progress : 0.008923672452984909
progress : 0.008929701961399087
progress : 0.008935731469813267
progress : 0.008941760978227445
progress : 0.008947790486641623
progress : 0.008953819995055803
progress : 0.008959849503469982
progress : 0.008965879011884162
progress : 0.00897190852029834
progress : 0.00897793802871252
progress : 0.008983967537126698
progress : 0.008989997045540876
progress : 0.008996026553955056
progress : 0.0

progress : 0.011829895508619181
progress : 0.011835925017033361
progress : 0.01184195452544754
progress : 0.01184798403386172
progress : 0.011854013542275898
progress : 0.011860043050690078
progress : 0.011866072559104256
progress : 0.011872102067518436
progress : 0.011878131575932614
progress : 0.011884161084346792
progress : 0.011890190592760972
progress : 0.01189622010117515
progress : 0.01190224960958933
progress : 0.011908279118003509
progress : 0.011914308626417689
progress : 0.011920338134831867
progress : 0.011926367643246047
progress : 0.011932397151660225
progress : 0.011938426660074403
progress : 0.011944456168488583
progress : 0.011950485676902762
progress : 0.011956515185316942
progress : 0.01196254469373112
progress : 0.0119685742021453
progress : 0.011974603710559478
progress : 0.011980633218973658
progress : 0.011986662727387836
progress : 0.011992692235802014
progress : 0.011998721744216194
progress : 0.012004751252630372
progress : 0.012010780761044552
progress : 0.01

progress : 0.014066843130279588
progress : 0.014072872638693766
progress : 0.014078902147107946
progress : 0.014084931655522125
progress : 0.014090961163936305
progress : 0.014096990672350483
progress : 0.014103020180764663
progress : 0.014109049689178841
progress : 0.014115079197593021
progress : 0.0141211087060072
progress : 0.014127138214421377
progress : 0.014133167722835557
progress : 0.014139197231249736
progress : 0.014145226739663916
progress : 0.014151256248078094
progress : 0.014157285756492274
progress : 0.014163315264906452
progress : 0.014169344773320632
progress : 0.01417537428173481
progress : 0.014181403790148988
progress : 0.014187433298563168
progress : 0.014193462806977346
progress : 0.014199492315391526
progress : 0.014205521823805705
progress : 0.014211551332219885
progress : 0.014217580840634063
progress : 0.014223610349048243
progress : 0.014229639857462421
progress : 0.0142356693658766
progress : 0.01424169887429078
progress : 0.014247728382704957
progress : 0.0

...

progress : 0.9863793404923696
progress : 0.9863853700007839
progress : 0.986391399509198
progress : 0.9863974290176122
progress : 0.9864034585260264
progress : 0.9864094880344405
progress : 0.9864155175428547
progress : 0.9864215470512689
progress : 0.986427576559683
progress : 0.9864336060680973
progress : 0.9864396355765115
progress : 0.9864456650849256
progress : 0.9864516945933398
progress : 0.986457724101754
progress : 0.9864637536101681
progress : 0.9864697831185824
progress : 0.9864758126269966
progress : 0.9864818421354107
progress : 0.9864878716438249
progress : 0.986493901152239
progress : 0.9864999306606532
progress : 0.9865059601690674
progress : 0.9865119896774815
progress : 0.9865180191858958
progress : 0.98652404869431
progress : 0.9865300782027241
progress : 0.9865361077111383
progress : 0.9865421372195525
progress : 0.9865481667279666
progress : 0.9865541962363809
progress : 0.9865602257447951
progress : 0.9865662552532092
progress : 0.9865722847616234
progress : 0.986

progress : 0.9893940946994592
progress : 0.9894001242078734
progress : 0.9894061537162875
progress : 0.9894121832247017
progress : 0.9894182127331159
progress : 0.98942424224153
progress : 0.9894302717499442
progress : 0.9894363012583584
progress : 0.9894423307667726
progress : 0.9894483602751868
progress : 0.9894543897836009
progress : 0.9894604192920151
progress : 0.9894664488004293
progress : 0.9894724783088434
progress : 0.9894785078172577
progress : 0.9894845373256719
progress : 0.989490566834086
progress : 0.9894965963425002
progress : 0.9895026258509144
progress : 0.9895086553593285
progress : 0.9895146848677427
progress : 0.989520714376157
progress : 0.9895267438845711
progress : 0.9895327733929853
progress : 0.9895388029013994
progress : 0.9895448324098136
progress : 0.9895508619182278
progress : 0.9895568914266419
progress : 0.9895629209350562
progress : 0.9895689504434704
progress : 0.9895749799518845
progress : 0.9895810094602987
progress : 0.9895870389687129
progress : 0.9

progress : 0.9939162260100934
progress : 0.9939222555185075
progress : 0.9939282850269218
progress : 0.993934314535336
progress : 0.9939403440437501
progress : 0.9939463735521643
progress : 0.9939524030605785
progress : 0.9939584325689926
progress : 0.9939644620774069
progress : 0.993970491585821
progress : 0.9939765210942352
progress : 0.9939825506026494
progress : 0.9939885801110635
progress : 0.9939946096194777
progress : 0.9940006391278919
progress : 0.994006668636306
progress : 0.9940126981447203
progress : 0.9940187276531345
progress : 0.9940247571615486
progress : 0.9940307866699628
progress : 0.994036816178377
progress : 0.9940428456867911
progress : 0.9940488751952054
progress : 0.9940549047036196
progress : 0.9940609342120337
progress : 0.9940669637204479
progress : 0.994072993228862
progress : 0.9940790227372762
progress : 0.9940850522456904
progress : 0.9940910817541045
progress : 0.9940971112625188
progress : 0.994103140770933
progress : 0.9941091702793471
progress : 0.994

progress : 0.9984383573207276
progress : 0.9984443868291418
progress : 0.998450416337556
progress : 0.9984564458459702
progress : 0.9984624753543844
progress : 0.9984685048627986
progress : 0.9984745343712127
progress : 0.9984805638796269
progress : 0.998486593388041
progress : 0.9984926228964552
progress : 0.9984986524048695
progress : 0.9985046819132836
progress : 0.9985107114216978
progress : 0.998516740930112
progress : 0.9985227704385261
progress : 0.9985287999469403
progress : 0.9985348294553545
progress : 0.9985408589637687
progress : 0.9985468884721829
progress : 0.9985529179805971
progress : 0.9985589474890112
progress : 0.9985649769974254
progress : 0.9985710065058396
progress : 0.9985770360142537
progress : 0.998583065522668
progress : 0.9985890950310821
progress : 0.9985951245394963
progress : 0.9986011540479105
progress : 0.9986071835563246
progress : 0.9986132130647388
progress : 0.998619242573153
progress : 0.9986252720815672
progress : 0.9986313015899814
progress : 0.99

NameError: name 'recommendations_per_user' is not defined

In [11]:
recommendations_per_user

NameError: name 'recommendations_per_user' is not defined

In [13]:
len(jobs_per_user)

20812